## Final Project Data Exploration

In [ ]:
# from google.colab import drive
# drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


**NAMES**: _Michelle Gottlieb Chernov, Aaron Armbruster, Jasper Wu, Gokul Deep, Nicole Gonzaga_

In [ ]:
import pandas as pd
import numpy as np
import altair as alt
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score
from sklearn.preprocessing import add_dummy_feature
import warnings
warnings.filterwarnings('ignore')

routes_raw = pd.read_csv('mp_routes.csv')

# Background Information

### Data Description

This data comes from a www.mountainproject.com which is a website that hosts information on over 100,000 rock climbing routes. The purpose of the site is to allow climbers to find routes in their area and from all over the world. The routes are posted by users along with as much information as they can furnish to help other climbers find the routes and allow them to bring the proper equipment. Each route has a location, name, type, grade, length, and rating. Both the rating and grade are choosen through user votes. The .csv file is from kaggle https://www.kaggle.com/datasets/pdegner/mountain-project-rotues-and-forums the kaggle poster wrote a python script the scraped mountain project for the routes.

### Variable Descriptions Of the Original CSV

**Route**: The name of the route which are often not unique.

**Location**: Where the route is located in a ascending fashion; going from most specific to less specific.

**URL**: Where the route is located on the site.

**Avg Stars**: Routes range from 0 - 4 stars, 0 being a terrible choss pile and 4 being fantastic. Stars can be given by users and this is the mean of the stars from the users who rated the route.

**Route Type**: In this project we will be focusing on Sport and Trad, but there are many different types including boulders, ice climbing, aid, and mixed. Sport climbs are climbs that have been equipped with bolts on the wall by the route developer for climbers to clip as they ascend the wall. Trad climbs have no pre-equiped protection so the climber places various equipment as they ascend which split into two groups active protection called cams and passive protection called nuts.

**Rating**: The difficulty of the climb. The climbs we will be exploring range from 5.0 - 5.15. The 5 is class level which usually means the climbing is technical and the climber should be belayed and place protection. Any fall from a class 5 can result in death or injury. What comes after the 5 is the difficulty with 5.0 being walking with a rope on and 5.15 being the hardest climbs in the world.

**Length**: The length of the route in meters.

**Pitches**: The amount of pitches. A pitch is the length of the climb that can be protected by one rope length. Most climbs are single pitches whereas some are multipitches requiring multiple belays to get to the top.

**Area Longitude**: The longitudinal coordinates of the climb.

**Area Latitude**: The latitudinal coordinates of the climb.

**Desc**: The route's description.

**Protection**: The protection required for the climb. Protection varies from climb to climb, with sport routes climbers need to know how many quickdraws to bring and trad climbing the climbers need to know what kind of rack to bring an active, passive or both.

**num_votes**: How many users have voted on how many stars to give the route.


Name | Variable description | Type
---|---|---
Name | Unique name of each climb trail | String
Location | Pathway of climbing trail and surronding area | String
Quality | Rating of each specific climb | Numeric
Type | Identifier of sport or traditional climbing route | String
Pitches | Amount of pitches per climb | Numeric
Length | Length of the route in meters | Numeric
Latitude | The latitudinal coordinates of the climb | Numeric
Longitude | The longitudinal coordinates of the climb | Numeric
Protection | Gear required for the climb | String
Votes | Amount of people rating climb | Numeric
Difficulty | Difficulty of each unique climb | Numeric

# Questions and Goals

**Difficulty and Quality**

Many climbers fall into the what are known as weekend warriors meaning the only time they can get out to climb is the weekend so often times climbers wonder where and what difficulty grades they should aim for to get the most out of their weekend. To be able to climb the upper grade levels it takes a lot of time and devotion for example going from climbing 5.12 to 5.13 might take multiple years worth of effort and specific training. Using visualization we hope to answer a few questions involving difficulty and the quality of the climb.

#### Question 1: 
How does the voting for quality vary with respect to the difficulty of the climb?

#### Approach:
Plot a histogram of quality against votes faceted by the difficulty range

**Climbing Type and Quality**

With many jobs offering full work from home options many climbers are leaving their expensive metropolitan areas with very little climbing to cheaper areas with tons of climbing. Using visualization we hope to explore the relationship between type of climb and quality. 

#### Questions 2: 
How many votes were observed relative to the quality and the route types traditional (trad) and sport?

#### Approach: 
Plot a histogram grouped by the type to see if there is a difference in voting across Quality.


**Length and Quality**

Using visualization we hope to explore the relationship length has on quality.

#### Question 3:
Does the length of the route affect the quality ?

#### Approach:
Plot a histogram of the length of the route versus its quality.

**Location and Quality**

By mapping, we can analyze the relationship between the climb's location and its quality.

#### Question 4:
Where are the highest quality routes located in the U.S.?

#### Approach:
Create a map to locate the climbs and differentiate their quality using a color scale.


**Linear Regression To Predict the Quality Rating of a Route**

Climbing routes are given a quality rating which is a number between zero and five. Using the data we accquired we hope to answer the question of how these climbs are given their quality rating. We would like examine how much of the quality rating comes from the extrinsic aspects of a climb. The extrinsic aspects are the routes location, type, length and difficulty so we will use these variables to answer our question and make the linear regression model.

The models we will consider:

$$Y_{Quality} = \beta_0 + \beta_1x_{location} + \beta_2x_{Type} + \beta_3x_{Difficulty} + \epsilon$$

$$Y_{Quality} = \beta_0 + \beta_1x_{location} + \beta_2x_{Type} + \beta_3x_{Difficulty} + \beta_4x_{Length} + \epsilon$$


#  Data Tidying 

To being our tidying process we will change a few variable names then drop variables and observations we are not interested in. The variables that we will change for the sake of brevity, familiarity and simplicty are route -> Name,  rating -> Grade,   avg_stars -> Quality, Route Type -> Type, num_votes -> Votes. We will drop all observations that are not simply called out as trad or Sport. The grades will have their letter grades dropped as the information is not relevant to our purposes.

In [ ]:
# Drop irrelevant columns
cols = [0,3,11]
routes_mod1 = routes_raw.drop(routes_raw.columns[cols],axis =1)

# routes_mod1.head()

In [ ]:
# Change column names
mapping = {"Route":"Name","Avg Stars": "Quality",routes_mod1.columns[3]:"Type",routes_mod1.columns[9]:"Protection",routes_mod1.columns[10]: "Votes",routes_mod1.columns[7]:"Latitude",routes_mod1.columns[8]:"Longitude"}
routes_mod2 = routes_mod1.rename(columns = mapping)
# routes_mod2.head()



In [ ]:
# Only keeping observations of trad or sport climbs

routes_mod3 = routes_mod2[(routes_mod2["Type"] =="Trad") | (routes_mod2["Type"] ==  "Sport")]

# routes_mod3.head()

In [ ]:
# Removing a, b, c, d, R, X, PG-13 keys from grades

routes_mod3.loc[:,"Grade"] = routes_mod3['Rating'].str[:4]
routes_mod3['Grade']= routes_mod3['Grade'].str.strip()
routes_mod3.loc[:,'Grade'] = routes_mod3['Grade'].str.replace("+","")
routes_mod3.loc[:,'Grade'] = routes_mod3['Grade'].str.replace("-","")

# Drop the rating column and keep our new Grade column
col = [4]
routes_mod4 = routes_mod3.drop(routes_mod3.columns[col],axis =1)

# routes_mod4.head()

In [ ]:
routes_mod4.Grade.unique()

array(['5.10', '5.9', '3rd', '4th', 'Easy', '5', '5.0', '5.1', '5.2',
       '5.3', '5.4', '5.5', '5.6', '5.7', '5.11', '5.12', '5.8', '5.13',
       '5.14', '5.15'], dtype=object)

In [ ]:
# We are only intrested in the 5th class climbs which are 5.0 and up
vals = ['3rd', '4th', 'Easy', '5']

routes_mod5 = routes_mod4.loc[~routes_mod4['Grade'].isin(vals)]

routes_mod5.head(2)

Name                                           Location  Quality  \
0  Access Denied  El Mirador > El Potrero Chico > Nuevo Leon > N...      2.9   
1   Agave Nectar  Sugar Shack > Cougar Canyon (Creek) - CONSTRUC...      2.0   

    Type  Pitches  Length  Latitude  Longitude  \
0  Sport        4   350.0  25.95044 -100.47755   
1  Sport        1     NaN  51.09642 -115.31767   

                                          Protection  Votes Grade  
0  12 draws + 60m Rope   Take 22 draws if you wan...     22  5.10  
1                                  4 bolts to anchor      1  5.10

In [ ]:
# We now have only the observations we are interested in
data = routes_mod5
data.Grade.unique()

array(['5.10', '5.9', '5.0', '5.1', '5.2', '5.3', '5.4', '5.5', '5.6',
       '5.7', '5.11', '5.12', '5.8', '5.13', '5.14', '5.15'], dtype=object)

# Plotting

### Histogram of Quality of a Climb VS Number of Votes split into level of difficulty


> Indented block



In [ ]:
# Let's do a random subset:
np.random.seed(40221) 
data2 = data.sample(n=5000)

# Let's make grade more understandable:
data2['Difficulty'] = data2['Grade'].str.split(".").str[1]
data2['Difficulty']=pd.to_numeric(data2['Difficulty'])
data2['filt_diff'] = (data2.loc[(data2['Difficulty'] <= 12) & (data2['Difficulty'] >= 9),:])['Difficulty']

hist2 = alt.Chart(data2).mark_bar().encode(
    x = alt.X('Quality', title = 'Quality'),
    y = alt.Y('Votes', title = 'Votes')
).properties(height=100,width=100).facet(column= alt.Column('filt_diff', title = 'Difficulty Range'))
hist2

alt.FacetChart(...)

### Relationship between Type of climbing technique and quality of climb on location

In [ ]:
first_loc = data.loc[:, 'Location'].str.split(">").str[0]
first_loc.nunique()

# Storing our filtered locations as a column:
data2['filt_loc'] = first_loc

data3 = data2.groupby(['filt_loc','Type']).mean()
data4 = data3.reset_index()

In [ ]:
# the right end is NOT INCLUDED in respective ranges for labels
data2['rounded_lat'] = data2['Latitude'].round()
data2
data2['rounded_long'] = data2['Longitude'].round()
labels = ["{0} - {1}".format(i, i+1) for i in range(0,5,1)]
data2['group'] = pd.cut(data2.Quality, range(0,6,1), right = False, labels = labels)
# data2.head()

In [ ]:
alt.Chart(data2).mark_bar().encode(
    x = alt.X('Type', title = 'Climb Type'),
    y = alt.Y('Votes', title = 'Vote Count')
).properties(height=100,width=150).facet(column=alt.Column('group', title='Quality Range'))

alt.FacetChart(...)

### Length of a climb compared to the quality

In [ ]:
qual = alt.Chart(data2.dropna(), title='Length vs Quality').mark_bar(opacity=.8).encode(
    y = alt.X('Length', title = 'Length'),
    x = alt.Y('Quality', title = 'Quality')
).project('albersUsa').properties(
    width=500,
    height=300
)

qual

alt.Chart(...)

### Location of Best Quality Climbs

In [ ]:
from vega_datasets import data
airports = data.airports()
states = alt.topo_feature(data.us_10m.url, feature='states')
airports = data.airports()

background = alt.Chart(states).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project('albersUsa').properties(
    width=800,
    height=600
)

foreground = alt.Chart(data2, title='Quality w/ Respect to US Map').mark_circle().encode(
    longitude='Longitude:Q',
    latitude='Latitude:Q',
    color=alt.Color('Quality', scale=alt.Scale(scheme='turbo'))
).project(
    "albersUsa"
).properties(
    width=800,
    height=600
)

background + foreground

alt.LayerChart(...)



# Model Building 

### Linear Regression Model for Quality using Location, Type, and Difficulty

In [ ]:
# dataset with columns of interest for prediction of Quality
x_df = data2.iloc[:, [1,2,3,4,5,6,7,11]]
loc_names = x_df.loc[:, 'Location'].str.split(">")
loc_names = loc_names.array

In [ ]:
# array of states
state_names = ["Alaska", "Alabama", "Arkansas", "American Samoa", "Arizona", "California", "Colorado", "Connecticut", "District of Columbia", "Delaware", "Florida", "Georgia", "Guam", "Hawaii", "Iowa", "Idaho", "Illinois", "Indiana", "Kansas", "Kentucky", "Louisiana", "Massachusetts", "Maryland", "Maine", "Michigan", "Minnesota", "Missouri", "Mississippi", "Montana", "North Carolina", "North Dakota", "Nebraska", "New Hampshire", "New Jersey", "New Mexico", "Nevada", "New York", "Ohio", "Oklahoma", "Oregon", "Pennsylvania", "Puerto Rico", "Rhode Island", "South Carolina", "South Dakota", "Tennessee", "Texas", "Utah", "Virginia", "Virgin Islands", "Vermont", "Washington", "Wisconsin", "West Virginia", "Wyoming"]

In [ ]:
# removing spaces at end of names in the location strings
for a in range(len(loc_names)):
  for i in range(len(loc_names[a])):
    loc_names[a][i]= loc_names[a][i].strip()

In [ ]:
# determining the state in the US for each relevant observations
for i in range(len(loc_names)):
  for x in range(len(loc_names[i])):
    for a in range(len(state_names)):
      if loc_names[i][x] == state_names[a]:
        loc_names[i].append(state_names[a])

In [ ]:
# extracting and assigning the last string for each Location 
for i in range(len(loc_names)):
  loc_names[i] = loc_names[i][-1]

In [ ]:
# assigning the last strings to a new column called "state"
x_df['state'] = loc_names
#removing the "non-state" columns
names = ['International', 'Puerto Rico', 'Virgin Islands']
x_df = x_df[x_df.state.isin(names) == False]

In [ ]:
# obtained from https://gist.github.com/sfirrin/fd01d87f022d80e98c37a045c14109fe
states_to_regions = {
    'Washington': 'West', 'Oregon': 'West', 'California': 'West', 'Nevada': 'West',
    'Idaho': 'West', 'Montana': 'West', 'Wyoming': 'West', 'Utah': 'West',
    'Colorado': 'West', 'Alaska': 'West', 'Hawaii': 'West', 'Maine': 'Northeast',
    'Vermont': 'Northeast', 'New York': 'Northeast', 'New Hampshire': 'Northeast',
    'Massachusetts': 'Northeast', 'Rhode Island': 'Northeast', 'Connecticut': 'Northeast',
    'New Jersey': 'Northeast', 'Pennsylvania': 'Northeast', 'North Dakota': 'Midwest',
    'South Dakota': 'Midwest', 'Nebraska': 'Midwest', 'Kansas': 'Midwest',
    'Minnesota': 'Midwest', 'Iowa': 'Midwest', 'Missouri': 'Midwest', 'Wisconsin': 'Midwest',
    'Illinois': 'Midwest', 'Michigan': 'Midwest', 'Indiana': 'Midwest', 'Ohio': 'Midwest',
    'West Virginia': 'South', 'District of Columbia': 'South', 'Maryland': 'South',
    'Virginia': 'South', 'Kentucky': 'South', 'Tennessee': 'South', 'North Carolina': 'South',
    'Mississippi': 'South', 'Arkansas': 'South', 'Louisiana': 'South', 'Alabama': 'South',
    'Georgia': 'South', 'South Carolina': 'South', 'Florida': 'South', 'Delaware': 'South',
    'Arizona': 'Southwest', 'New Mexico': 'Southwest', 'Oklahoma': 'Southwest',
    'Texas': 'Southwest'}

In [ ]:
# assigning regions for each observation based on which region their state is in
regions = []
for i in range(len(x_df['state'])):
  regions.append(states_to_regions[x_df['state'].iloc[i]])

x_df['Region'] = regions
x_df.head()

KeyError: ignored

In [ ]:
# remove strings and quantitative columns
reg_data = x_df.copy().drop(columns = ['Location', 'Pitches', 'Latitude', 'Longitude', 'state', 'Length'])

# reorder Region
reg_data['Region'] = reg_data.Region.astype('category')

reg_data['Region'] = reg_data.Region.cat.as_ordered().cat.reorder_categories(['West', 'Midwest', 'Southwest', 'South', 'Northeast'])

# reorder gender
reg_data['Type'] = reg_data.Type.astype('category')
reg_data['Type'] = reg_data.Type.cat.as_ordered().cat.reorder_categories(['Sport', 'Trad'])

# reorder difficulty
reg_data['Difficulty'] = reg_data.Difficulty.astype('category')
reg_data['Difficulty'] = reg_data.Difficulty.cat.as_ordered().cat.reorder_categories([0,1,2,3,4,5,6,7,8,9,10,11,12,13,14])

reg_data.head()

In [ ]:
x_df2 = pd.get_dummies(reg_data, drop_first = True).drop(columns = 'Quality')

In [ ]:
x_mx = add_dummy_feature(x_df2,value = 1)
y = reg_data['Quality']

In [ ]:
mlr = LinearRegression(fit_intercept = False)
mlr.fit(x_mx, y)

In [ ]:
# store dimensions
n, p = x_mx.shape
# compute x'x
xtx = x_mx.transpose().dot(x_mx)
# compute x'x inverse
xtx_inv = np.linalg.inv(xtx)
# compute residuals
resid = y - mlr.predict(x_mx)
# compute error variance estimate
sigmasqhat = ((n - 1)/(n - p)) * resid.var()
# compute variance-covariance matrix
v_hat = xtx_inv * sigmasqhat
# compute standard errors
coef_se = np.append((v_hat.diagonal())**(1/2), float('nan'))
# coefficient labels
coef_labels =  np.append(x_df2.columns,['intercept', 'error_variance'])
# estimates
coef_estimates = np.append(mlr.coef_, sigmasqhat)
# summary table
coef_table = pd.DataFrame(
    data = {'coefficient estimate': coef_estimates, 'standard error': coef_se},
    index= coef_labels
)
# print
coef_table

In [ ]:
# determining accuracy of model using R^2 computation 
R_2 = (y.var() - resid.var())/y.var()

R_2

### Linear Regression Model for Quality using Location, Type, Location, and Difficulty

In [ ]:
data_mod1 = data2[data2["Location"].str.contains("International")==False]

def label_states (row):
    if any(i in row['Location'] for i in  ['Maine','New Hampshire','Vermont','Massachusetts','Rhode Island','Connecticut','New York','Pennsylvania','New Jersey','Delaware','Maryland']):
        return 'Northeast' 
    elif any(i in row['Location'] for i in ['Wisconsin','Michigan','Illinois','Indiana','Ohio','North Dakota','South Dakota','Nebraska','Kansas','Minnesota','Iowa','Missouri']):
        return 'Midwest'
    elif any(i in row['Location'] for i in ['District of Columbia','Virginia','West Virginia','North Carolina','South Carolina','Georgia','Florida','Kentucky','Tennessee','Mississippi', 'Alabama','Arkansas','Louisiana']):
        return 'Southeast'
    elif any(i in row['Location'] for i in ['Oklahoma','Texas','New Mexico',"Arizona"]):
        return 'Southwest'
    elif any(i in row['Location'] for i in ['Colorado',"Wyoming","Montana","Idaho","Utah","Nevada","Oregon","Washington",'California',"Hawaii",'Alaska']):
        return 'West'
    else:
        return 'International'


data_mod1['Region'] = data_mod1.apply(lambda row: label_states(row), axis=1)

In [ ]:

data_mod2 = data_mod1.dropna()


reg_data = data_mod2.copy().drop(columns = ['Name', 'Location','Quality','Pitches','Protection','Votes','Grade','filt_diff','filt_loc','rounded_lat','rounded_long','group','Latitude','Longitude'])


In [ ]:
# reorder Region
reg_data['Region'] = reg_data.Region.astype('category')

reg_data['Region'] = reg_data.Region.cat.as_ordered().cat.reorder_categories(['West', 'Midwest', 'Southwest', 'Southeast', 'Northeast'])

# reorder gender
reg_data['Type'] = reg_data.Type.astype('category')
reg_data['Type'] = reg_data.Type.cat.as_ordered().cat.reorder_categories(['Sport', 'Trad'])

# reorder difficulty
reg_data['Difficulty'] = reg_data.Difficulty.astype('category')
reg_data['Difficulty'] = reg_data.Difficulty.cat.as_ordered().cat.reorder_categories([9,10,11,12])



x_df = pd.get_dummies(reg_data, drop_first = True,columns = ['Region','Type','Difficulty'])
x_df

x_df1 = x_df.dropna()

x_mx = add_dummy_feature(x_df1, value = 1)
y = data_mod2.Quality

In [ ]:
mlr = LinearRegression(fit_intercept = False)
mlr.fit(x_mx, y)

LinearRegression(fit_intercept=False)

In [ ]:
# store dimensions
n, p = x_mx.shape

# compute x'x
xtx = x_mx.transpose().dot(x_mx)

# compute x'x inverse
xtxinv = np.linalg.inv(xtx)

# compute residuals
resid = y - mlr.predict(x_mx)

# compute error variance estimate
sigmasqhat = resid.var()*(n - 1)/(n - p)

# compute variance-covariance matrix
v_hat = sigmasqhat*xtxinv

# compute standard errors
coef_se = np.sqrt(v_hat.diagonal())
coef_se = np.append(coef_se, float('nan'))

# coefficient labels
coef_labels = np.append(np.append('intercept', x_df.columns.values), 'error variance')

# estimates
coef_estimates = np.append(mlr.coef_, sigmasqhat)

# summary table
coef_table = pd.DataFrame(
    {'estimate': coef_estimates,'standard error': coef_se},
    index = coef_labels
)

# print
coef_table

estimate  standard error
intercept         2.054105        0.046519
Length            0.001132        0.000137
Region_Midwest    0.362628        0.068918
Region_Southwest  0.027548        0.045533
Region_Southeast  0.162287        0.044999
Region_Northeast  0.087530        0.060981
Type_Trad         0.044433        0.032820
Difficulty_10     0.220616        0.047001
Difficulty_11     0.447551        0.048492
Difficulty_12     0.768690        0.053024
error variance    0.517058             NaN

In [ ]:
R_2 = r2_score(y, mlr.predict(x_mx))

R_2

0.13140080941448262